# Text Embedding
In this notebook, we generate 10-K filings text embeddings with the Vertex AI [text-embedding](https://ai.google.dev/gemini-api/docs/models/gemini#text-embedding) model.  Unstructured text from 10-K filings has been extracted using a parser beforehand.

In this notebook, we will:
1. Get 10-K filings unstructured text from a Google storage bucket
2. specifically select Item 1 from the 10K which describes the business of the company: who and what the company does, what subsidiaries it owns, and what markets it operates in. 
3. Chunk the text into natural sections (to avoid input token limits)
4. Save text with embeddings to csv to stage for loading into graph

In [36]:
%pip install --user tabulate sentence-transformers
%pip install --user altair

  Using cached sentence_transformers-3.1.0-py3-none-any.whl.metadata (23 kB)
  Using cached transformers-4.44.2-py3-none-any.whl.metadata (43 kB)
  Using cached torch-2.4.1-cp310-cp310-manylinux1_x86_64.whl.metadata (26 kB)
  Using cached nvidia_cuda_nvrtc_cu12-12.1.105-py3-none-manylinux1_x86_64.whl.metadata (1.5 kB)
  Using cached nvidia_cuda_runtime_cu12-12.1.105-py3-none-manylinux1_x86_64.whl.metadata (1.5 kB)
  Using cached nvidia_cuda_cupti_cu12-12.1.105-py3-none-manylinux1_x86_64.whl.metadata (1.6 kB)
  Using cached nvidia_cudnn_cu12-9.1.0.70-py3-none-manylinux2014_x86_64.whl.metadata (1.6 kB)
  Using cached nvidia_cublas_cu12-12.1.3.1-py3-none-manylinux1_x86_64.whl.metadata (1.5 kB)
  Using cached nvidia_cufft_cu12-11.0.2.54-py3-none-manylinux1_x86_64.whl.metadata (1.5 kB)
  Using cached nvidia_curand_cu12-10.3.2.106-py3-none-manylinux1_x86_64.whl.metadata (1.5 kB)
  Using cached nvidia_cusolver_cu12-11.4.5.107-py3-none-manylinux1_x86_64.whl.metadata (1.6 kB)
  Using cached nvi

Be sure to restart the kernel after you run the pip command.

## Get 10-K Filings from Google Cloud Storage

In [1]:
from google.cloud import storage

storage_client = storage.Client()
storage_client.bucket('neo4j-datasets').blob('hands-on-lab/form10k.zip').download_to_filename('/home/jupyter/form10k.zip')

In [2]:
!mkdir /home/jupyter/form10k
!unzip -qq -n '/home/jupyter/form10k.zip' -d /home/jupyter/form10k

mkdir: cannot create directory ‘/home/jupyter/form10k’: File exists


## 10-K Filings Exploration and Chunking
Let's open one file to understand its contents.  It is actually a json file. 

In [3]:
import json
with open('/home/jupyter/form10k/0001830197-22-000038.txt') as f:
    f10_k = json.load(f)

We are interested in Item 1 specifically. 

Item 1 describes the business of the company: who and what the company does, what subsidiaries it owns, and what markets it operates in. It may also include recent events, competition, regulations, and labor issues. (Some industries are heavily regulated, and have complex labor requirements, which have significant effects on the business.) Other topics in this section may include special operating costs, seasonal factors, or insurance matters.

In [4]:
len(f10_k['item1'])

241333

This text has the ability to exceed token limits for the embedding model.  Also the quality of embeddings can go down if the text gets too large. As such we should find some way to chunk the text up into seperate sections for embedding.

Below is a way to do this with Langchain's `RecursiveCharacterTextSplitter` which takes into account of Chunk overlaps. 

In [5]:
from langchain.text_splitter import RecursiveCharacterTextSplitter

text = f10_k['item1']

text_splitter = RecursiveCharacterTextSplitter(
    chunk_size = 2000,
    chunk_overlap  = 15,
    length_function = len,
    is_separator_regex = False,
)
docs = text_splitter.split_text(text)

In [6]:
print(docs[0])

>Item 1. Business 
Company Overview
We are a leading residential mortgage originator and servicer driven by a mission to create financially healthy, happy homeowners. We do this by delivering scale, efficiency and savings to our partners and customers. Our business model is focused on leveraging a nationwide network of partner relationships to drive sustainable origination growth. We support our origination operations through a robust operational infrastructure and a highly responsive customer experience. We then leverage our servicing platform to manage the customer experience. We believe that the complementary relationship between our origination and servicing businesses allows us to provide a best-in-class experience to our customers throughout their homeownership lifecycle.
Our primary focus is our Wholesale channel, which is a business-to-business-to-customer distribution model in which we utilize our relationships with independent mortgage brokerages, which we refer to as our Bro

## Get 10-K Text Embeddings with Vertex AI
Now that we understand our data and how to chunk it.  Let's Generate embeddings.

In [20]:
from vertexai.language_models import TextEmbeddingModel
EMBEDDING_MODEL = TextEmbeddingModel.from_pretrained("text-embedding-004")

In [21]:
# We will need a chunking utility to stay within token limits as we loop through files
def chunks(xs, n=3):
    n = max(1, n)
    return [xs[i:i + n] for i in range(0, len(xs), n)]

In [22]:
import time

def create_text_embedding_entries(input_text:str, company_name: str, cusip: str):
    text_splitter = RecursiveCharacterTextSplitter(
        chunk_size = 2000,
        chunk_overlap  = 15,
        length_function = len,
        is_separator_regex = False,
    )
    docs = text_splitter.split_text(input_text)
    res = []
    seq_id = -1
    for d in chunks(docs):
        embeddings = EMBEDDING_MODEL.get_embeddings(d)
        
        # throttle so we don't blow through the quota.
        time.sleep(1)
        
        for i in range(len(d)):
            seq_id += 1
            res.append({'companyName': company_name, 'cusip': cusip, 'seqId': seq_id, 'contextId': company_name + str(seq_id), 'textEmbedding': embeddings[i].values, 'text': d[i]})
    return res

Due to Quota Limitations, lets only do 5 form 10k files out of the 95 we have

In [23]:
import os

file_names = os.listdir('/home/jupyter/form10k/')[0:5]
len(file_names)

5

This cell takes about 15 minutes to run.  That's largely down to us throttling so we don't exceed the quota on our free account.  If you're using an enterprise account, you won't need to throttle like this.

In [24]:
%%time

count = 0
embedding_entries = []
for file_name in file_names:
    if '.txt' in file_name:
        count += 1
        if count % 5 == 0:
            print(f'Parsed {count} of {len(file_names)}')
        with open('/home/jupyter/form10k/' + file_name) as f:
            f10_k = json.load(f)
        embedding_entries.extend(create_text_embedding_entries(f10_k['item1'], f10_k['companyName'], f10_k['cusip']))
len(embedding_entries)

Parsed 5 of 5
CPU times: user 1.26 s, sys: 69.6 ms, total: 1.33 s
Wall time: 1min 42s


261

## Save 10-K Documents with Embeddings
We will save these locally to use in graph loading, in the next part.

In [25]:
import pandas as pd
edf = pd.DataFrame(embedding_entries)

In [26]:
edf

companyName      cusip  seqId                   contextId  \
0           General motors co  369604103      0          General motors co0   
1           General motors co  369604103      1          General motors co1   
2           General motors co  369604103      2          General motors co2   
3           General motors co  369604103      3          General motors co3   
4           General motors co  369604103      4          General motors co4   
..                        ...        ...    ...                         ...   
256  OLD POINT FINANCIAL CORP  679580100     40  OLD POINT FINANCIAL CORP40   
257  OLD POINT FINANCIAL CORP  679580100     41  OLD POINT FINANCIAL CORP41   
258  OLD POINT FINANCIAL CORP  679580100     42  OLD POINT FINANCIAL CORP42   
259  OLD POINT FINANCIAL CORP  679580100     43  OLD POINT FINANCIAL CORP43   
260  OLD POINT FINANCIAL CORP  679580100     44  OLD POINT FINANCIAL CORP44   

                                         textEmbedding  \
0    [0.005074136890470982, 0.01391859445720911, 0....   
1    [0.003213596995919943, -0.010261103510856628, ...   
2    [-0.028832055628299713, 0.0019998974166810513,...   
3    [-0.0017784348456189036, -0.022517859935760498...   
4    [0.045161452144384384, 0.048554353415966034, -...   
..                                                 ...   
256  [-0.018077075481414795, 0.024025849997997284, ...   
257  [0.0019837208092212677, -0.007150125224143267,...   
258  [-0.014449276961386204, 0.019032035022974014, ...   
259  [0.01426299661397934, 0.02891477756202221, 0.0...   
260  [-0.018711932003498077, 0.05975503847002983, 0...   

                                                  text  
0    >Item 1. Business \nGeneral Motors Company (so...  
1    Our vision for the future is a world with zero...  
2    In September 2021, we announced three new driv...  
3    Ultium Charge 360 is also available to our fle...  
4    We offer OnStar and connected services to more...  
..                                                 ...  
256  Volcker Rule.\n The Dodd-Frank Act prohibits b...  
257  In December 2018, consistent with the provisio...  
258  Index\n\n\n\n\n\n\n\n\nCongress also enacted t...  
259  As with other financial institutions, the earn...  
260  Future Regulation\n. From time to time, variou...  

[261 rows x 6 columns]

Provide your Neo4j credentials.  We need the DB conection URL, the username (probably `neo4j`), and your password.

In [27]:
# username is neo4j by default
NEO4J_USERNAME = 'neo4j'

# You will need to change these to match your credentials
NEO4J_URI = 'neo4j+s://7e098dc5.databases.neo4j.io' #Eg 'neo4j+s://ccc5f4f5.databases.neo4j.io'
NEO4J_PASSWORD = '19_Kt_bHLte_0F2r4OAqGv1ihz9ciXJfJaav0-hpNrI'

In [28]:
from graphdatascience import GraphDataScience

gds = GraphDataScience(
    NEO4J_URI,
    auth=(NEO4J_USERNAME, NEO4J_PASSWORD),
    aura_ds=True
)
gds.set_database('neo4j')

Remember to create indexes. We will be merging 10K documents by `companyName`. In a production setting, we would want to use a better identifier here (like we did with cusip for Company) However, this should suffice for our intents and purposes as we are just getting acquainted to learning about semantic search.

In [29]:
gds.run_cypher('CREATE INDEX company_name IF NOT EXISTS FOR (n:Company) ON (n.companyName)')
gds.run_cypher('CREATE CONSTRAINT unique_document_id IF NOT EXISTS FOR (n:Document) REQUIRE (n.documentId) IS NODE KEY')

Empty DataFrame
Columns: []
Index: []

Due to the size of the documents we will want to transform the dataframe into a list of dict that we can chunk up and insert via parameterized query.

In [30]:
emb_entries = edf.to_dict(orient='records')

In [31]:
total = len(emb_entries)
count = 0
for d in chunks(emb_entries, 100):
    gds.run_cypher('''
    UNWIND $records AS record
    MATCH(c:Company {cusip:record.cusip})
    MERGE(b:Document {documentId:record.contextId})
    SET b.documentType = 'FORM_10K_ITEM1', b.seqId = record.seqId, b.textEmbedding = record.textEmbedding, b.text = record.text
    MERGE(c)-[:HAS]->(b)
    RETURN count(b) as cnt
    ''', params = {'records':d})
    count += len(d)
    print(f'loaded {count} of {total}')

loaded 100 of 261
loaded 200 of 261
loaded 261 of 261


## Check Data

In [32]:
# Check node count
gds.run_cypher('MATCH(doc:Document) RETURN count(doc)')

count(doc)
0         261

Note that we were only getting 10-K docs for a minority of companies. It should be fine for this, but in a more rigorous setting, you may want to try and pull more.  There are likely a few factors attributing to this. 

1. We used company names to search EDGAR which resulted in many misses and dups which were discarded. In a more rigorous setting, we would investigate other endpoints and use more parsing to extract EDGAR cik keys for exact matching companies when pulling forms.

2. Company names are not consistent across form13 filings, so even if we successfully pull on one version of a company name, we may not be able to merge it into the graph via the one company name represented there. 

3. Not all companies in the dataset are obligated to file 10-Ks.

In [33]:
# Check count and percentage of companies with 10-K docs.  Note it is the minority
gds.run_cypher('''
MATCH(b:Company)
WITH b, count{(b)-[:HAS]->(d:Document)} AS docCount
WITH count(b) AS total, sum(toInteger(docCount > 0)) AS numWithDocs
RETURN total, numWithDocs, round(100*toFloat(numWithDocs)/toFloat(total), 2) As PercWithDocs
''')

total  numWithDocs  PercWithDocs
0  15841            4          0.03

You might note that there are duplicate names.  For our purposes here, we will treat it as entity resolution, meaning that we treat companies with the same name as belonging to the same overarching entity for semantic search. In a more rigorous setting, we would need to disambiguate with other EDGAR keys.

In [34]:
# Show duplicates via HAS relationship
gds.run_cypher('''
MATCH(b:Company)
RETURN count(b) AS totalCompanies, count(DISTINCT b.companyName) AS uniqueCompanyNames
''')

totalCompanies  uniqueCompanyNames
0           15841               10673

## View Embeddings as Clusters

Vector embeddings generated by language models are nothing but numerical representation of words or sentences.  So, similar sentences will be located nearby.  The embeddings we generated earlier are higher dimensional ones.  To visualize them, we need to reduce the dimensionality.  Let's do that and visualize it.

In [37]:
import altair as alt

def generate_chart(df, xcol, ycol, lbl = 'on', color = 'basic', title = '', tooltips = ['documentId'], label = ''):
  chart = alt.Chart(df).mark_circle(size=30).encode(
    x = alt.X(xcol,
        scale=alt.Scale(zero = False),
        axis=alt.Axis(labels = False, ticks = False, domain = False)
    ),
    y = alt.Y(ycol,
        scale=alt.Scale(zero = False),
        axis=alt.Axis(labels = False, ticks = False, domain = False)
    ),
    color= alt.value('#333293') if color == 'basic' else color,
    tooltip=tooltips
    )

  if lbl == 'on':
    text = chart.mark_text(align = 'left', baseline = 'middle', dx = 7, size = 5, color = 'black').encode(text = label, color = alt.value('black'))
  else:
    text = chart.mark_text(align = 'left', baseline = 'middle', dx = 10).encode()

  result = (chart + text).configure(background="#FDF7F0"
        ).properties(
        width = 800,
        height = 500,
        title = title
       ).configure_legend(
  orient = 'bottom', titleFontSize = 18, labelFontSize = 18)
        
  return result

In [38]:
# Reduce dimensionality using PCA
from sklearn.decomposition import PCA

# Function to return the principal components
def get_pc(arr, n):
  pca = PCA(n_components = n)
  embeds_transform = pca.fit_transform(arr)
  return embeds_transform

In [39]:
emb_df = gds.run_cypher("MATCH (c:Company)-[:HAS]->(n:Document) RETURN c.companyName as companyName, n.documentId as documentId, n.text as text, n.textEmbedding as emb LIMIT 1000")
emb_df

companyName                            documentId  \
0               Applied Materials   APPLIED INDUSTRIAL TECHNOLOGIES IN0   
1               Applied Materials   APPLIED INDUSTRIAL TECHNOLOGIES IN1   
2               Applied Materials  APPLIED INDUSTRIAL TECHNOLOGIES IN10   
3               Applied Materials  APPLIED INDUSTRIAL TECHNOLOGIES IN11   
4               Applied Materials  APPLIED INDUSTRIAL TECHNOLOGIES IN12   
..                            ...                                   ...   
256  OLD DOMINION FREIGHT LINE IN             OLD POINT FINANCIAL CORP5   
257  OLD DOMINION FREIGHT LINE IN             OLD POINT FINANCIAL CORP6   
258  OLD DOMINION FREIGHT LINE IN             OLD POINT FINANCIAL CORP7   
259  OLD DOMINION FREIGHT LINE IN             OLD POINT FINANCIAL CORP8   
260  OLD DOMINION FREIGHT LINE IN             OLD POINT FINANCIAL CORP9   

                                                  text  \
0    >ITEM 1. \nBUSINESS.\nIn this annual report on...   
1    •\nApplied's Board of Directors Governance Pri...   
2    We report results of operations in two segment...   
3    Service center locations are stocked with prod...   
4    .  Our Fluid Power & Flow Control segment incl...   
..                                                 ...   
256  The Company also faces competitive pressure fr...   
257  Trust faces intense competition in all aspects...   
258  The Company maintains a website on the Interne...   
259  COVID-19\n\n\n\n\n\n\nSince the first quarter ...   
260  Index\n\n\n\n\n\n\n\n\nEstimates for the allow...   

                                                   emb  
0    [-0.009522206149995327, 0.006157139781862497, ...  
1    [0.007960875518620014, 0.02018204890191555, -0...  
2    [-0.017254266887903214, 0.009162823669612408, ...  
3    [-0.024197788909077644, -0.004841284826397896,...  
4    [-0.04279713332653046, -0.0012587984092533588,...  
..                                                 ...  
256  [0.057833798229694366, 0.057400431483983994, 0...  
257  [0.04345279559493065, 0.03198039531707764, 0.0...  
258  [0.027021972462534904, 0.02471899427473545, -0...  
259  [0.019741928204894066, 0.023331336677074432, -...  
260  [0.02385258860886097, 0.02568201534450054, -0....  

[261 rows x 4 columns]

## K-Means Clustering on the Embeddings
Let's run the K-Means Clustering algorithm and view similar document chunks. 

In [40]:
import numpy as np
from sklearn.cluster import KMeans

embeds = np.array(emb_df['emb'].tolist())
embeds_pc2 = get_pc(embeds, 2)

df_clust = pd.concat([emb_df, pd.DataFrame(embeds_pc2)], axis = 1)
n_clusters = 5

kmeans_model = KMeans(n_clusters = n_clusters, n_init = 1, random_state = 0)
classes = kmeans_model.fit_predict(embeds).tolist()
df_clust['cluster'] = (list(map(str,classes)))

df_clust.columns = df_clust.columns.astype(str)
generate_chart(df_clust.iloc[:],'0', '1', lbl = 'off', color = 'cluster', title = 'K-Means Clustering with n Clusters', tooltips = ['documentId', 'text'], label = '')


alt.LayerChart(...)